# size distribution example
Load basic packages

In [1]:
import size_distribution_class as sdc
import statistics

import pandas as pd
import pandas_bokeh
import numpy as np
from bokeh.io import output_file, output_notebook
from bokeh.models import DatetimeTickFormatter, ranges, Span, Label, Range1d, LinearAxis
from bokeh.plotting import figure, show
from bokeh.layouts import gridplot
from bokeh.palettes import linear_palette, Turbo256
pd.set_option('plotting.backend', 'pandas_bokeh')
output_notebook(hide_banner=True)
from IPython.core.display import display, HTML


In [2]:
psd = sdc.singeFileProcess( verbose=True )

Please select the directory with the source image tiles.  2.9141 x 2.9141 nm/px
 Analysing C2-C3S 28d cryoBIB_004-cut.tif
--------------------------------------------------
 ...processing particle #500/1114
 ...processing particle #1000/1114
 Analysed particles: 988, ignored 0-values: 126, finished in 993 ms
     file_index   diameter   area  surface        volume
0           0.0   4.296740   14.5     58.0     41.535152
1           0.0   1.128379    1.0      4.0      0.752253
2           0.0   1.595769    2.0      8.0      2.127692
3           0.0   2.256758    4.0     16.0      6.018022
4           0.0   2.393654    4.5     18.0      7.180961
..          ...        ...    ...      ...           ...
983         0.0  29.250931  672.0   2688.0  13104.417162
984         0.0  17.186959  232.0    928.0   2658.249725
985         0.0  31.280738  768.5   3074.0  16026.164935
986         0.0   4.583498   16.5     66.0     50.418476
987         0.0   7.442172   43.5    174.0    215.822980

[988 

basic functions to generate the following diagrams

In [3]:
def get_X_List( values ):
    value_cnt = len(values)
    x_range = list(range(value_cnt))
    x_range.pop(0)
    x_range.append(value_cnt)
    return x_range
    
def getLineDiagram_mean_type2(title, plot_width=1200, legend_location='top_right'):
    p = figure(title=title, y_axis_type="log", plot_width=plot_width, y_range=(1, psd.psd_df['area'].max()), plot_height=600, background_fill_color="#fafafa")
    #p.left[0].formatter.use_scientific = False

    p.xaxis.axis_label = 'area in'
    p.yaxis.axis_label = 'phase content in %'
    
    x_range = get_X_List( list(psd.psd_df['area']) )
    
    colors = linear_palette(Turbo256, 2)

    p.line(x_range, psd.psd_df['area'], line_color=colors[1], line_width=2, legend_label='Test')

    p.legend.location = legend_location
    show(p)

def get_histogram(dist_type='cld', column='diameter', max_value=1000, plot_width=1200, legend_location='top_right'):
    if dist_type == 'psd':
        df = psd.psd_df
        dist_name = 'pore size distribution'
    else:
        df = psd.cld_df
        dist_name = 'chord length distribution'
    
    unit = psd.scaling['unit']
    power = 1

    if column == 'area' or column == 'surface':
        unit += '²'
        power = 2
    elif column == 'volume':  
        unit += '³'
        power = 3

    title = '{} as {} up to {} {}'.format(dist_name, column, max_value, unit)
    x_label = 'pore size ({}) in {}'.format(column, unit)
    y_label = 'phase content in %'

    hist, bins = psd.get_histogram_list( df[column], max_value, power=power )
    hist = hist/(np.sum(hist)/100)
    #psd.clean_histogram(hist,bins,power)
    sum_list = psd.get_sum_list(hist)

    p = figure(title=title,  plot_width=plot_width, y_range=(0,np.amax(hist)), plot_height=600, background_fill_color="#fafafa")#y_axis_type="log",
    #p.left[0].formatter.use_scientific = False

    p.xaxis.axis_label = x_label
    #p.yaxis.axis_label = y_label

    p.quad(bottom=0, top=hist, left=bins[1:], right=bins[:-1], fill_color="navy", line_color="navy")
    
    p.extra_y_ranges = {"sum_line": Range1d(start=0, end=np.amax(sum_list))}

    p.line(bins, sum_list, line_color="#ff8888", line_width=4, alpha=0.7, legend_label="Sum", y_range_name="sum_line")
    p.add_layout(LinearAxis(y_range_name="sum_line",axis_label=y_label), 'left')
    #p.line(bins, cdf, line_color="orange", line_width=2, alpha=0.7, legend_label="CDF")

    p.legend.location = legend_location
    show(p)

generate Diagrams 

In [4]:
get_histogram('cld','area', max_value=500000)

68 67
[1.1656400e+01 4.0797401e+01 9.6165298e+01 1.8941660e+02 3.2929340e+02
 5.2162408e+02 7.8097919e+02 1.1102726e+03 1.5240748e+03 2.0282144e+03
 2.6343474e+03 3.3512163e+03 4.1846494e+03 5.1492168e+03 6.2478330e+03
 7.4950679e+03 8.8967510e+03 1.0464537e+04 1.2204256e+04 1.4130477e+04
 1.6246113e+04 1.8562824e+04 2.1092264e+04 2.3840262e+04 2.6815559e+04
 3.0029811e+04 3.3494680e+04 3.7213070e+04 4.1196648e+04 4.5454148e+04
 4.9997234e+04 5.4831727e+04 5.9969285e+04 6.5418656e+04 7.1188578e+04
 7.7284875e+04 8.3722125e+04 9.0509070e+04 9.7651531e+04 1.0515825e+05
 1.1304381e+05 1.2131112e+05 1.2997474e+05 1.3903759e+05 1.4851716e+05
 1.5841345e+05 1.6874103e+05 1.7950862e+05 1.9072500e+05 2.0239889e+05
 2.1454195e+05 2.2715709e+05 2.4025889e+05 2.5385611e+05 2.6795744e+05
 2.8256872e+05 2.9770456e+05 3.1337078e+05 3.2957609e+05 3.4632925e+05
 3.6364484e+05 3.8152578e+05 3.9998369e+05 4.1902734e+05 4.3866547e+05
 4.5890969e+05 4.7976591e+05 5.0000434e+05] [1.3292647243238724, 2.0398

In [5]:
get_histogram('psd','volume',900)

99 98
[  0.       2.9141   5.8282   8.7423  11.6564  17.4846  20.3987  23.3128
  26.2269  32.0551  34.9692  37.8833  43.7115  49.5397  52.4538  58.282
  64.1102  67.0243  72.8525  78.6807  84.5089  90.3371  96.1653 101.9935
 107.8217 113.6499 119.4782 125.3064 131.1346 139.8769 145.7051 151.5333
 160.2756 166.1038 171.932  180.6743 186.5025 195.2448 201.073  209.8153
 215.6435 224.3858 233.1281 238.9563 247.6986 256.4409 265.1832 273.9255
 279.7537 288.496  297.2383 305.9806 314.7229 332.2075 340.9498 349.6922
 358.4344 367.1767 375.919  384.6614 396.3178 405.06   413.8024 422.5447
 434.2011 442.9434 451.6856 463.342  472.0844 480.8267 492.4831 501.2254
 512.8818 521.6241 533.2805 542.0228 553.6792 562.4215 585.7343 606.133
 617.7894 626.5318 638.1882 649.8446 661.501  670.2433 681.8996 693.5561
 705.2124 728.5252 760.5804 795.5496 821.7765 833.4329 845.0894 856.7457
 868.4022 891.715  903.3713] [13.915416098226466, 2.1828103683492497, 7.503410641200546, 3.819918144611187, 3.0013642564

In [6]:
get_histogram('cld','diameter', max_value=2000)

UnboundLocalError: local variable 'pow_bins' referenced before assignment

In [7]:
get_histogram('psd','diameter',100)

UnboundLocalError: local variable 'pow_bins' referenced before assignment